## Import libraries

In [1]:
from bs4 import BeautifulSoup
import requests
import pandas as pd
import numpy as np

In [2]:
def getInnings(UID):
    URL = 'http://www.millenniumcricketleague.com/Home/ShowScore.aspx?schid=' + str(UID)
    page = requests.get(URL)

    soup = BeautifulSoup(page.content, 'html.parser')
    table = soup.find('table')
    table_data= table.find_all('tr')
    
    headings1=[]
    for i in table_data[3].find_all("h4"):
        headings1.append(i.text.replace('\n', ' ').strip())
        
    headings1.pop(0)
    headings1.insert(0, "x")
    headings1.insert(1, "y")
        
    headings2=['Bowling',
             'Overs',
             'Mdns',
             'Runs',
             'Wkts',
             'Wides',
             'NBs',
             'Econ']
    
    headings=np.concatenate((headings1,headings2))
    
    final_table_data=[]
    for tr in table_data:
        t_row = {}
        for td, th in zip(tr.find_all("td"), headings):
             t_row[th] = td.text.replace('\n', ' ').strip()
        final_table_data.append(t_row)
        
        df = pd.DataFrame(final_table_data)
        df["UID"] =uid
    return(df)

## Extracting and Parsing Data from URL

In [3]:
URL = 'http://www.millenniumcricketleague.com/Home/Results.aspx?si=19&tt=1'
page = requests.get(URL)

soup = BeautifulSoup(page.content, 'html.parser')
table = soup.find('table')

In [4]:
table_data= table.find_all('tr')
x=table_data[0].find_all("tr")

In [5]:
headings=[]
for i in x[0].find_all("th"):
    headings.append(i.text.replace('\n', ' ').strip())

In [6]:
headings

['#', 'Date', 'Match', 'Division', 'Ground', 'Umpire(s)', 'Results']

In [7]:
x1=table_data[0].find_all("td")
mtch=[]
mtchType=[]
matchRound=[]
for i in x1[0].find_all("div" , class_="MatchType"):
    mtch.append(i.text.replace('\n', ' ').strip())
    if i.find("span")["id"][39:44] == 'ctl00':
        typ='ctl00'
    elif i.find("span")["id"][39:44] == 'ctl01':
        typ='ctl01'
    elif i.find("span")["id"][39:44] == 'ctl02':
        typ='ctl02'
    elif i.find("span")["id"][39:44] == 'ctl03':
        typ='ctl03'
    else:
        pass
    mtchType.append(typ)
    
    dict1 = {}
    for a, b in zip(mtchType, mtch):
        dict1[a] = b
matchRound.append(dict1)

In [8]:
matchRound

[{'ctl00': 'Results - 2019 - Forty 40                                                                                                                                                                                                                                                        - Finals',
  'ctl01': 'Results - 2019 - Forty 40                                                                                                                                                                                                                                                        - Semi Finals',
  'ctl02': 'Results - 2019 - Forty 40                                                                                                                                                                                                                                                        - Quarter Finals',
  'ctl03': 'Results - 2019 - Forty 40                                                              

In [9]:
final_table_data=[]
for tr in table.find_all("tr"):
    t_row = {}
    for td, th in zip(tr.find_all("td"), headings):
        attr=td.find_next().attrs
        t_row[th] = td.text.strip()
        if attr.get("id") != None and attr.get("id")[39:44] in matchRound[0].keys():
            t_row["Round"] = (matchRound[0].get(attr.get("id")[39:44]))
        if attr.get("href") != None and "ShowScore.aspx?schid" in attr.get("href"):
            t_row["UID"] = attr.get("href")[21:]
    final_table_data.append(t_row)

In [10]:
df = pd.DataFrame(final_table_data)

In [11]:
pd.set_option('display.max_rows', None)
pd.set_option('display.max_colwidth', -1)

# Data Cleaning

In [12]:
df=df.drop(df.index[18:54])
df = df.dropna()
df=df.drop(df.index[0])

In [13]:
df['Umpire(s)']= df['Umpire(s)'].str.replace('\n\n',',')

In [14]:
df['Umpire(s)']= df['Umpire(s)'].str.replace('\n','')

In [15]:
df['Match']= df['Match'].str.replace('Vs\n',' Vs ')

In [16]:
df=df.reset_index(drop=True)

In [17]:
df=df.rename(columns={'#':"Position"})

In [18]:
df

Position         Date Division                       Ground  \
0    2        09/21 10:30  B        Weston Road 1                 
1    1        09/14 11:30  A        Mercer County Park 2          
2    2        09/14 11:30  A        North Brunswick - Indus       
3    3        09/14 11:30  B        Weston Road 2                 
4    4        09/14 11:30  B        Weston Road 1                 
5    1        09/07 11:00  B        Old Bridge                    
6    2        09/07 11:30  A        Mercer County Park 2          
7    3        09/07 11:30  A        Williams Park                 
8    4        09/07 11:30  A        John Phillips Park            
9    5        09/07 11:30  B        Weston Road 2                 
10   6        09/07 11:30  B        Weston Road 1                 
11   7        09/07 12:00  A        Howe Athletic Complex         
12   8        09/07 12:00  B        Johnson Park Pitch- 1         
13   1        04/20 11:30  A        Avenue K                      
14   2        04/20 11:30  A        Mercer County Park 2          
15   3        04/20 12:00  A        Kilmer Field                  
16   4        04/20 12:00  B        Old Bridge                    
17   5        04/20 12:00  B        Kawameeh Park                 
18   6        04/20 12:00  B        Warinanco Park                
19   1        04/27 10:30  A        Mercer County Park 2          
20   2        04/27 11:30  A        Rowland Park                  
21   3        04/27 11:30  A        Mercer County Park 4          
22   4        04/27 11:30  A        Kennedy Park                  
23   5        04/27 11:30  A        Avenue K                      
24   6        04/27 11:30  A        North Brunswick - Indus       
25   7        04/27 11:30  A        Stallions                     
26   8        04/27 11:30  B        Weston Road 2                 
27   9        04/27 11:30  B        Johnson Park Pitch- 3         
28   10       04/27 11:30  B        Princeton Cricket ground      
29   11       04/27 11:30  B        Volunteers Park               
30   12       04/27 11:30  B        John Phillips Park            
31   13       04/27 11:30  B        Old Bridge                    
32   14       04/27 11:30  B        Lincoln Park                  
33   15       04/27 11:30  B        Weston Road 1                 
34   16       04/27 12:00  A        Woodrow Wilson 1              
35   1        05/04 11:30  A        Avenue K                      
36   2        05/04 11:30  A        Weston Road 1                 
37   3        05/04 11:30  A        Stallions                     
38   4        05/04 11:30  A        North Brunswick - Indus       
39   5        05/04 11:30  A        Mercer County Park 2          
40   6        05/04 11:30  B        Old Bridge                    
41   7        05/04 11:30  B        Weston Road 2                 
42   8        05/04 11:30  B        Rowland Park                  
43   9        05/04 11:30  B        Johnson Park Pitch- 1         
44   10       05/04 12:00  A        Howe Athletic Complex         
45   11       05/04 12:00  A        Williams Park                 
46   12       05/04 12:00  A        Johnson Park Pitch- 3         
47   13       05/04 12:00  B        Plainsboro Park               
48   14       05/04 12:00  B        Woodrow Wilson 2              
49   15       05/04 12:00  B        Kawameeh Park                 
50   16       05/04 12:00  B        Thomas Jefferson 2 - Edison   
51   1        05/11 11:00  B        John Phillips Park            
52   2        05/11 11:30  A        Avenue K                      
53   3        05/11 11:30  A        Mercer County Park 4          
54   4        05/11 11:30  A        Weston Road 1                 
55   5        05/11 11:30  A        Mercer County Park 2          
56   6        05/11 11:30  B        Tall Timbers Park             
57   7        05/11 11:30  B        Lincoln Park                  
58   8        05/11 11:30  B        Old Bridge     

In [19]:
writer = pd.ExcelWriter('ScrappedData.xlsx')
df.to_excel(writer, index=False)
writer.save()

In [20]:
battingTable = []
bowlingTable = []
extasTable = []
for uid in df["UID"]:
    finalDf=getInnings(uid)
    for index, row in finalDf.iterrows():
        if  "Innings" in row['x'] and "R" == row['y']:
            startIdx =index
        if row['x'] == "Extras":
            endIdx= index
            battingTable.append(finalDf[startIdx:endIdx])

    for index, row in finalDf.iterrows():
        if  "Bowling" == row['x'] :
            startIdx1 =index
        if "Notes" in row['x'] and pd.isnull(finalDf['y'][index]) :
            endIdx1= index
            bowlingTable.append(finalDf[startIdx1:endIdx1])
            
    for index, row in finalDf.iterrows():
        if (row['x'] == "Extras"):
            newRow=row
            extasTable.append(newRow.values)

battingTable = pd.concat(battingTable)
battingTable=battingTable.reset_index(drop=True)
#battingTable.columns = battingTable.iloc[0]
battingTable = battingTable.dropna(axis=1, how='all')
battingTable=battingTable.reset_index(drop=True)
#battingTable.columns = ["4s", "6s", "B", "R", "SR", "Player", "Details", "UID"]

bowlingTable = pd.concat(bowlingTable)
bowlingTable=bowlingTable.reset_index(drop=True)
bowlingTable.columns = bowlingTable.iloc[0]
bowlingTable = bowlingTable.drop(bowlingTable[bowlingTable["Bowling"] == "Bowling"].index)
bowlingTable = bowlingTable.dropna(axis=1, how='all')
bowlingTable = bowlingTable.dropna()
bowlingTable=bowlingTable.reset_index(drop=True)
bowlingTable.columns.values[8] = "UID"

extasTable = pd.DataFrame(extasTable, columns=finalDf.columns).reset_index()
extasTable = extasTable.dropna(axis=1, how='all')

In [20]:
battingTable

4s  6s    B    R       SR  \
0     6s  SR  4s   B    NaN       
1     3   0   15   18   120       
2     7   4   81   84   103.7     
3     3   6   35   62   177.14    
4     1   1   16   17   106.25    
5     0   2   21   25   119.05    
6     2   0   26   23   88.46     
7     0   1   5    10   200       
8     1   1   7    14   200       
9     2   2   19   29   152.63    
10    0   1   14   15   107.14    
11    0   0   3    5    166.67    
12    6s  SR  4s   B    NaN       
13    5   3   31   44   141.94    
14    3   1   31   26   83.87     
15    4   1   45   36   80        
16    1   1   32   25   78.12     
17    2   1   11   19   172.73    
18    0   0   9    2    22.22     
19    0   1   8    7    87.5      
20    1   0   5    5    100       
21    0   0   7    0    0         
22    0   0   5    3    60        
23    0   0   1    0    0         
24    6s  SR  4s   B    NaN       
25    4   3   64   55   85.94     
26    1   1   36   14   38.89     
27    7   2   64   70   109.38    
28    0   0   0    1    N/A       
29    1   4   47   48   102.13    
30    0   0   0    3    N/A       
31    0   0   0    13   N/A       
32    0   0   0    5    N/A       
33    0   0   0    0    N/A       
34    0   0   0    0    N/A       
35    0   0   0    0    N/A       
36    6s  SR  4s   B    NaN       
37    0   0   0    0    N/A       
38    5   4   56   71   126.79    
39    3   2   26   28   107.69    
40    0   0   0    6    N/A       
41    0   0   0    0    N/A       
42    6   2   40   45   112.5     
43    0   0   0    3    N/A       
44    0   0   0    1    N/A       
45    0   0   0    0    N/A       
46    0   0   0    6    N/A       
47    0   0   0    1    N/A       
48    6s  SR  4s   B    NaN       
49    1   1   6    10   166.67    
50    3   10  0    96   N/A       
51    0   0   0    0    N/A       
52    7   10  0    117  N/A       
53    1   0   0    21   N/A       
54    2   1   0    22   N/A       
55    0   0   0    0    N/A       
56    2   0   0    10   N/A       
57    0   0   0    0    N/A       
58    0   0   0    9    N/A       
59    0   0   0    0    N/A       
60    6s  SR  4s   B    NaN       
61    7   0   0    51   N/A       
62    0   0   0    9    N/A       
63    0   0   0    0    N/A       
64    1   5   0    56   N/A       
65    1   2   0    24   N/A       
66    0   0   0    0    N/A       
67    1   3   0    26   N/A       
68    3   6   0    73   N/A       
69    0   0   0    11   N/A       
70    0   0   0    0    N/A       
71    0   0   0    0    N/A       
72    6s  SR  4s   B    NaN       
73    4   11  85   101  118.82    
74    6   3   22   45   204.55    
75    1   1   54   22   40.74     
76    1   0   7    12   171.43    
77    3   4   26   51   196.15    
78    1   0   7    8    114.29    
79    0   0   8    5    62.5      
80    1   0   3    5    166.67    
81    0   0   1    0    0         
82    0   0   4    4    100       
83    0   0   5    0    0         
84    6s  SR  4s   B    NaN       
85    3   3   32   49   153.12    
86    2   0   9    9    100       
87    2   0   18   10   55.56     
88    1   0   51   30   58.82     
89    3   1   28   42   150       
90    10  8   36   100  277.78    
91    2   0   18   10   55.56     
92    2   1   14   19   135.71    
93    1   0   2    4    200       
94    0   0   0    0    N/A       
95    0   0   0    0    N/A       
96    6s  SR  4s   B    NaN       
97    1   0   19   11   57.89     
98    2   1   43   30   69.77     
99    1   0   12   10   83.33     
100   0   0   0    100  N/A       
101   4   0   28   26   92.86     
102   0   0   6    4    66.67     
103   0   0   0    20   N/A       
104   0   0   2    1    50        
105   0   0   1    0    0         
106   0   0   0    4    N/A       
107   0   0   0    7    N/A       
108   6s  SR  4s   B    NaN       
109   0   0   1    0    0         
110   6   1   69   54   78.26     
111   0   0   3    1    33.33     
112   1   0   35   12   34.29     
113   1   2   40

In [21]:
battingTable.columns = ["4s", "6s", "B", "R", "SR", "Player", "Details", "UID"]

In [22]:
battingTable['Innings'] = '' 
for i, row in enumerate(battingTable.itertuples(), 1):
    if row.Details =='R':
        startIdx = i
        endIdx = i + 11
    
        battingTable['Innings'][startIdx:endIdx] = row.Player

In [23]:
battingTable = battingTable.drop(battingTable[battingTable["Details"] == "R"].index)

In [24]:
battingTable

4s  6s    B    R       SR  \
1     3   0   15   18   120       
2     7   4   81   84   103.7     
3     3   6   35   62   177.14    
4     1   1   16   17   106.25    
5     0   2   21   25   119.05    
6     2   0   26   23   88.46     
7     0   1   5    10   200       
8     1   1   7    14   200       
9     2   2   19   29   152.63    
10    0   1   14   15   107.14    
11    0   0   3    5    166.67    
13    5   3   31   44   141.94    
14    3   1   31   26   83.87     
15    4   1   45   36   80        
16    1   1   32   25   78.12     
17    2   1   11   19   172.73    
18    0   0   9    2    22.22     
19    0   1   8    7    87.5      
20    1   0   5    5    100       
21    0   0   7    0    0         
22    0   0   5    3    60        
23    0   0   1    0    0         
25    4   3   64   55   85.94     
26    1   1   36   14   38.89     
27    7   2   64   70   109.38    
28    0   0   0    1    N/A       
29    1   4   47   48   102.13    
30    0   0   0    3    N/A       
31    0   0   0    13   N/A       
32    0   0   0    5    N/A       
33    0   0   0    0    N/A       
34    0   0   0    0    N/A       
35    0   0   0    0    N/A       
37    0   0   0    0    N/A       
38    5   4   56   71   126.79    
39    3   2   26   28   107.69    
40    0   0   0    6    N/A       
41    0   0   0    0    N/A       
42    6   2   40   45   112.5     
43    0   0   0    3    N/A       
44    0   0   0    1    N/A       
45    0   0   0    0    N/A       
46    0   0   0    6    N/A       
47    0   0   0    1    N/A       
49    1   1   6    10   166.67    
50    3   10  0    96   N/A       
51    0   0   0    0    N/A       
52    7   10  0    117  N/A       
53    1   0   0    21   N/A       
54    2   1   0    22   N/A       
55    0   0   0    0    N/A       
56    2   0   0    10   N/A       
57    0   0   0    0    N/A       
58    0   0   0    9    N/A       
59    0   0   0    0    N/A       
61    7   0   0    51   N/A       
62    0   0   0    9    N/A       
63    0   0   0    0    N/A       
64    1   5   0    56   N/A       
65    1   2   0    24   N/A       
66    0   0   0    0    N/A       
67    1   3   0    26   N/A       
68    3   6   0    73   N/A       
69    0   0   0    11   N/A       
70    0   0   0    0    N/A       
71    0   0   0    0    N/A       
73    4   11  85   101  118.82    
74    6   3   22   45   204.55    
75    1   1   54   22   40.74     
76    1   0   7    12   171.43    
77    3   4   26   51   196.15    
78    1   0   7    8    114.29    
79    0   0   8    5    62.5      
80    1   0   3    5    166.67    
81    0   0   1    0    0         
82    0   0   4    4    100       
83    0   0   5    0    0         
85    3   3   32   49   153.12    
86    2   0   9    9    100       
87    2   0   18   10   55.56     
88    1   0   51   30   58.82     
89    3   1   28   42   150       
90    10  8   36   100  277.78    
91    2   0   18   10   55.56     
92    2   1   14   19   135.71    
93    1   0   2    4    200       
94    0   0   0    0    N/A       
95    0   0   0    0    N/A       
97    1   0   19   11   57.89     
98    2   1   43   30   69.77     
99    1   0   12   10   83.33     
100   0   0   0    100  N/A       
101   4   0   28   26   92.86     
102   0   0   6    4    66.67     
103   0   0   0    20   N/A       
104   0   0   2    1    50        
105   0   0   1    0    0         
106   0   0   0    4    N/A       
107   0   0   0    7    N/A       
109   0   0   1    0    0         
110   6   1   69   54   78.26     
111   0   0   3    1    33.33     
112   1   0   35   12   34.29     
113   1   2   40   24   60        
114   9   2   53   93   175.47    
115   0   0   10   5    50        
116   1   0   5    7    140       
117   1   1   14   19   135.71    
118   0   0   6    7    116.67    
119   0   0   1    2    200       
121   0   0   13   4    30.77     
122   0   0   10   5    50        
123   0   0   17   8    47.06     
124   0   0   21

In [25]:
writer = pd.ExcelWriter('Batting.xlsx')
battingTable.to_excel(writer, index=False)
writer.save()

In [26]:
bowlingTable

0    Wkts Wides Runs   Econ Mdns NBs  \
0     0    4     62   12.40  0    1    
1     4    7     63   7.88   0    0    
2     1    5     42   7.00   0    0    
3     0    0     21   21.00  0    0    
4     2    0     55   6.88   0    0    
5     1    4     35   5.00   0    1    
6     1    2     48   9.60   0    0    
7     0    0     18   4.50   0    0    
8     0    0     26   8.67   0    0    
9     0    1     45   7.50   0    1    
10    2    10    39   7.80   0    0    
11    3    3     16   2.67   1    0    
12    4    5     43   7.17   0    0    
13    2    4     32   4.00   1    0    
14    0    2     16   4.00   0    0    
15    1    4     65   8.12   0    0    
16    1    5     25   3.12   1    0    
17    2    2     30   3.75   0    0    
18    0    2     40   10.00  0    0    
19    1    0     29   7.25   1    0    
20    0    0     43   10.75  0    0    
21    2    0     30   3.75   0    0    
22    1    0     16   3.20   0    0    
23    2    0     40   6.67   0    0    
24    3    0     10   2.50   0    0    
25    3    5     63   7.88   0    0    
26    2    2     53   8.83   0    0    
27    4    2     53   6.62   0    0    
28    0    1     30   7.50   0    0    
29    1    2     47   5.88   0    0    
30    0    2     53   8.83   0    0    
31    0    0     44   6.29   0    0    
32    0    0     32   6.40   0    0    
33    4    0     50   6.25   0    0    
34    1    0     44   7.33   0    0    
35    2    0     26   8.67   0    0    
36    1    0     9    4.50   0    0    
37    2    0     58   8.29   0    0    
38    0    5     43   10.75  0    1    
39    0    3     23   11.50  0    1    
40    3    1     58   8.29   0    0    
41    0    2     20   5.00   0    0    
42    2    1     61   8.71   0    1    
43    3    0     31   4.43   0    0    
44    1    0     49   6.12   0    0    
45    0    5     33   11.00  0    0    
46    2    2     66   8.25   0    0    
47    1    2     47   7.83   0    0    
48    1    0     51   6.38   0    1    
49    1    0     42   7.00   0    0    
50    1    1     34   11.33  0    0    
51    1    0     10   N/A    0    0    
52    2    4     39   4.88   0    0    
53    2    5     35   4.38   0    0    
54    2    1     42   6.00   0    0    
55    1    2     29   3.62   0    0    
56    0    0     17   17.00  0    0    
57    0    4     30   7.50   0    0    
58    1    1     21   5.25   0    0    
59    2    2     18   2.25   0    0    
60    2    5     42   5.25   0    0    
61    0    0     23   4.60   0    0    
62    1    0     47   5.88   0    0    
63    0    0     12   12.00  0    0    
64    2    0     58   8.29   0    0    
65    0    0     24   12.00  0    0    
66    2    4     7    1.75   1    0    
67    3    8     31   4.43   0    0    
68    3    4     27   3.38   1    0    
69    0    0     17   8.50   0    0    
70    1    0     14   4.67   0    0    
71    1    4     20   2.50   1    0    
72    2    0     19   9.50   0    0    
73    0    0     22   5.50   0    0    
74    1    1     13   4.33   0    0    
75    1    0     18   6.00   0    0    
76    0    2     6    6.00   0    0    
77    2    6     50   7.14   0    0    
78    1    5     66   8.25   0    0    
79    0    3     58   7.25   0    0    
80    0    3     32   6.40   0    0    
81    2    4     26   4.33   0    0    
82    0    0     12   12.00  0    0    
83    1    5     42   8.40   0    0    
84    1    0     30   10.00  0    0    
85    1    3     31   5.17   0    0    
86    3    2     38   7.60   0    0    
87    3    1     30   3.75   0    0    
88    0    0     39   7.80   0    0    
89    0    0     22   7.33   0    0    
90    0    0     28   5.60   0    0    
91    1    0     28   7.00   0    0    
92    1    0     23   2.88   0    1    
93    4    0     26   5.20   0    1    
94    1    0     23   3.83   0    1    
95    0    0     27   5.40   0    1    
96    0    0     24   3.43   0    1    
97    3    0     16   3.20   0    1    
98    1    1     23   7.67   0    0    


In [27]:
writer = pd.ExcelWriter('Bowling_new.xlsx')
bowlingTable.to_excel(writer, index=False)
writer.save()

In [28]:
extasTable

index B    R       x  \
0    0        27   Extras   
1    1        20   Extras   
2    2        19   Extras   
3    3        7    Extras   
4    4        14   Extras   
5    5        23   Extras   
6    6        32   Extras   
7    7        14   Extras   
8    8        17   Extras   
9    9        7    Extras   
10   10       18   Extras   
11   11       7    Extras   
12   12       26   Extras   
13   13       6    Extras   
14   14       7    Extras   
15   15       4    Extras   
16   16       24   Extras   
17   17       20   Extras   
18   18       9    Extras   
19   19       37   Extras   
20   20       28   Extras   
21   21       7    Extras   
22   22       27   Extras   
23   23       9    Extras   
24   24       31   Extras   
25   25       4    Extras   
26   26       0    Extras   
27   27       0    Extras   
28   28       0    Extras   
29   29       0    Extras   
30   30       0    Extras   
31   31       0    Extras   
32   32       0    Extras   
33   33       0    Extras   
34   34       23   Extras   
35   35       23   Extras   
36   36       0    Extras   
37   37       0    Extras   
38   38       22   Extras   
39   39       47   Extras   
40   40       20   Extras   
41   41       8    Extras   
42   42       22   Extras   
43   43       20   Extras   
44   44       24   Extras   
45   45       6    Extras   
46   46       28   Extras   
47   47       30   Extras   
48   48       27   Extras   
49   49       11   Extras   
50   50       24   Extras   
51   51       25   Extras   
52   52       24   Extras   
53   53       27   Extras   
54   54       19   Extras   
55   55       35   Extras   
56   56       20   Extras   
57   57       26   Extras   
58   58       0    Extras   
59   59       0    Extras   
60   60       20   Extras   
61   61       28   Extras   
62   62       0    Extras   
63   63       0    Extras   
64   64       27   Extras   
65   65       9    Extras   
66   66       22   Extras   
67   67       13   Extras   
68   68       8    Extras   
69   69       6    Extras   
70   70       19   Extras   
71   71       30   Extras   
72   72       18   Extras   
73   73       4    Extras   
74   74       21   Extras   
75   75       33   Extras   
76   76       12   Extras   
77   77       11   Extras   
78   78       7    Extras   
79   79       23   Extras   
80   80       30   Extras   
81   81       10   Extras   
82   82       17   Extras   
83   83       17   Extras   
84   84       18   Extras   
85   85       6    Extras   
86   86       32   Extras   
87   87       14   Extras   
88   88       14   Extras   
89   89       7    Extras   
90   90       17   Extras   
91   91       15   Extras   
92   92       32   Extras   
93   93       16   Extras   
94   94       12   Extras   
95   95       13   Extras   
96   96       10   Extras   
97   97       15   Extras   
98   98       16   Extras   
99   99       9    Extras   
100  100      13   Extras   
101  101      20   Extras   
102  102      11   Extras   
103  103      30   Extras   
104  104      53   Extras   
105  105      29   Extras   
106  106      16   Extras   
107  107      33   Extras   
108  108      12   Extras   
109  109      16   Extras   
110  110      26   Extras   
111  111      13   Extras   
112  112      15   Extras   
113  113      33   Extras   
114  114      22   Extras   
115  115      41   Extras   
116  116      18   Extras   
117  117      26   Extras   
118  118      30   Extras   
119  119      14   Extras   
120  120      22   Extras   
121  121      21   Extras   
122  122      27   Extras   
123  123      10   Extras   
124  124      16   Extras   
125  125      8    Extras   
126  126      30   Extras   
127  127      8    Extras   
128  128      23   Extras   
129  129      15   Extras   
130  130      27   Extras   
131  131      25   Extras   
132  132      25   Extras   
133  133      12   Extras   
134  134      20   Extras   
135  135      24   Extras   
136  136      11   Extras   
137

In [29]:
extasTable=extasTable.drop(['index', 'B', 'R', 'x'], axis=1)
extasTable['y']= extasTable['y'].str.replace('(','')
extasTable['y']= extasTable['y'].str.replace(')','')
extasTable[["byes","legbyes", "wides", "noballs", "penalty"]]= extasTable["y"].str.split(",", expand = True)
extasTable=extasTable.drop(['y'], axis=1)
for i in extasTable.columns.values:
    if i !="UID":
        for j in extasTable[i]:
            if i in j:
                extasTable[i]= extasTable[i].str.replace(i+':','')

In [30]:
extasTable

UID byes legbyes wides noballs penalty
0    4726  1     2       22    2       0    
1    4726  0     0       19    1       0    
2    4715  0     0       19    0       0    
3    4715  7     0       0     0       0    
4    4716  0     0       14    0       0    
5    4716  12    11      0     0       0    
6    4717  2     15      12    3       0    
7    4717  2     1       10    1       0    
8    4718  0     0       17    0       0    
9    4718  0     0       7     0       0    
10   4695  2     0       16    0       0    
11   4695  0     0       7     0       0    
12   4696  0     0       26    0       0    
13   4696  0     0       6     0       0    
14   4697  1     0       0     6       0    
15   4697  1     0       3     0       0    
16   4699  1     1       20    2       0    
17   4699  0     9       11    0       0    
18   4692  0     1       8     0       0    
19   4692  10    6       21    0       0    
20   4693  2     1       25    0       0    
21   4693  0     0       7     0       0    
22   4698  3     0       22    2       0    
23   4698  1     0       8     0       0    
24   4694  0     3       27    1       0    
25   4694  0     0       4     0       0    
26   4449  0     0       0     0       0    
27   4449  0     0       0     0       0    
28   4453  0     0       0     0       0    
29   4453  0     0       0     0       0    
30   4452  0     0       0     0       0    
31   4452  0     0       0     0       0    
32   4454  0     0       0     0       0    
33   4454  0     0       0     0       0    
34   4455  3     1       18    1       0    
35   4455  0     0       21    2       0    
36   4456  0     0       0     0       0    
37   4456  0     0       0     0       0    
38   4465  5     5       12    0       0    
39   4465  8     11      17    6       5    
40   4458  0     0       19    1       0    
41   4458  2     0       6     0       0    
42   4459  0     0       19    3       0    
43   4459  1     0       18    1       0    
44   4460  5     6       12    1       0    
45   4460  1     0       5     0       0    
46   4461  8     0       19    1       0    
47   4461  13    2       15    0       0    
48   4462  0     2       20    5       0    
49   4462  1     1       9     0       0    
50   4463  0     10      14    0       0    
51   4463  10    6       9     0       0    
52   4457  1     2       15    6       0    
53   4457  1     0       25    1       0    
54   4466  0     11      8     0       0    
55   4466  8     10      17    0       0    
56   4467  0     5       14    1       0    
57   4467  3     6       16    1       0    
58   4468  0     0       0     0       0    
59   4468  0     0       0     0       0    
60   4469  3     4       11    2       0    
61   4469  1     2       25    0       0    
62   4470  0     0       0     0       0    
63   4470  0     0       0     0       0    
64   4472  0     8       17    2       0    
65   4472  0     2       6     1       0    
66   4687  0     0       20    2       0    
67   4687  0     0       13    0       0    
68   4464  0     1       6     1       0    
69   4464  0     0       5     1       0    
70   4473  0     1       17    1       0    
71   4473  1     2       26    1       0    
72   4477  4     0       13    1       0    
73   4477  1     1       2     0       0    
74   4478  5     2       14    0       0    
75   4478  0     0       31    2       0    
76   4479  0     0       10    2       0    
77   4479  0     0       10    1       0    
78   4480  0     0       7     0       0    
79   4480  15    8       0     0       0    
80   4482  2     2       26    0       0    
81   4482  0     0       10    0       0    
82   4484  0     6       9     2       0    
83   4484  5     0       12    0       0    
84   4486  0     0       16    2       0    
85   4486  0     0       6     0       0    
86   4487  6     0       25    1       0    
87   4487  0     1       13    0       0    
8

In [26]:
writer = pd.ExcelWriter('Extras_new.xlsx')
extasTable.to_excel(writer, index=False)
writer.save()